In [107]:
import xgboost as xgb
#import lightgbm
#import matplotlib.pyplot as plt
import warnings
import pandas as pd
import numpy as np
import optuna
from sklearn.feature_selection import mutual_info_classif
#from catboost import CatBoostClassifier, Pool
from sklearn.base import clone
from optuna.samplers import TPESampler
from optuna.integration import XGBoostPruningCallback,LightGBMPruningCallback
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split, GridSearchCV, StratifiedKFold, RandomizedSearchCV, cross_val_score, StratifiedGroupKFold, TimeSeriesSplit, cross_validate
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import SVC
from sklearn.preprocessing import LabelEncoder, StandardScaler, PowerTransformer, OrdinalEncoder
from sklearn.neural_network import MLPClassifier
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import SimpleImputer, KNNImputer, IterativeImputer
from sklearn.preprocessing import OneHotEncoder, MinMaxScaler, RobustScaler
from sklearn.compose import ColumnTransformer
from sklearn.linear_model import LogisticRegression, BayesianRidge
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix, f1_score,make_scorer

In [123]:
df = pd.read_csv('train_set.csv')
df['Fight_ID']
for index, row in df.iterrows():
    df_anteriores = df.iloc[0:index]
    df_anteriores_inverso = df_anteriores.iloc[::-1]
    contador_a = 1
    contador_b = 1
    for index2,row2 in df_anteriores_inverso.iterrows():
        if row2['Fighter_A_Name'] == row['Fighter_A_Name']:
            if ['Fighter_A_Is_Debut']==1:
            row[f'fa_lag{contador']==row['Winner_A']
            fa = True
                

0 Fighter_A_Name                                              Johnny Rhodes
Fighter_B_Name                                              Patrick Smith
Date                                                           1994-03-11
Weight_Class                                                        Other
Title_Bout                                                              0
                                                    ...                  
Fighter_B_Days_Since_Last_Fight                                       0.0
Winner_A                                                                0
Fighter_A_Is_Debut                                                      1
Fighter_B_Is_Debut                                                      1
Fight_ID                           johnny-rhodes_patrick-smith_1994-03-11
Name: 0, Length: 72, dtype: object
1 Fighter_A_Name                                              Royce Gracie
Fighter_B_Name                                             Jason DeLucia
D

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Fighter_A_Name                                               Jared Cannonier
Fighter_B_Name                                                Jan Blachowicz
Date                                                              2017-12-16
Weight_Class                                               Light Heavyweight
Title_Bout                                                                 0
                                                     ...                    
Fighter_B_Days_Since_Last_Fight                                         56.0
Winner_A                                                                   0
Fighter_A_Is_Debut                                                         0
Fighter_B_Is_Debut                                                         0
Fight_ID                           jared-cannonier_jan-blachowicz_2017-12-16
Name: 4428, Length: 72, dtype: object
4429 Fighter_A_Name                                                 Robbie Lawler
Fighter_B_Name                   

In [61]:
df = pd.read_csv('train_set.csv')
#df = df.iloc[4923:]
#df.drop(df[df['Weight_Class'].isin(['Catch Weight', 'Other'])].index, inplace=True)
#df[df['Weight_Class'] == 'Catch Weight']
#df[df['Weight_Class'] == 'Other']
#df.drop(df[df['Weight_Class'].isin(['Catch Weight', 'Other'])].index, inplace=True)
df.drop(['Fighter_A_Name', 'Fighter_B_Name', 'Date',
         'Referee', 'Location', 'Country', 'Continent', 'Season', 'Fight_ID'], axis=1, inplace=True)
#features_a_quitar=['Fighter_B_Sig_Str_Landed_Body', 'Fighter_A_Sig_Str_Landed_Body', 'Fighter_A_Totals_Rev', 'Fighter_B_Totals_Rev', 'Fighter_B_Is_Debut', 'Fighter_A_Is_Debut', 'Fighter_B_Sig_Str_Attempted_Leg', 'Fighter_A_Sig_Str_Attempted_Leg', 'Fighter_A_Is_Debut', 'Fighter_B_Is_Debut', 'Fighter_B_Draws', 'Fighter_A_Draws', 'Fighter_A_Draws', 'Fighter_B_Draws', 'Fighter_A_Sig_Str_Landed_Body', 'Fighter_B_Sig_Str_Landed_Body', 'Fighter_B_Sig_Str_Attempted_Clinch', 'Fighter_A_Sig_Str_Attempted_Clinch', 'Fighter_B_Totals_Rev', 'Fighter_A_Totals_Rev', 'Fighter_A_Sig_Str_Attempted_Clinch', 'Fighter_B_Sig_Str_Attempted_Clinch', 'Fighter_A_Sig_Str_Attempted_Leg', 'Fighter_B_Sig_Str_Attempted_Leg']
#df.drop(inplace=True, columns=features_a_quitar)
df = df[(df["Fighter_A_Is_Debut"] != 1) | (df["Fighter_B_Is_Debut"] != 1)]
y = df['Winner_A']
df2 = df.copy()
df2.drop(['Winner_A'], inplace = True, axis = 1)
df.drop(['Winner_A'], inplace = True, axis = 1)

'''X_2 = []
df2.drop('Winner_A', axis=1, inplace =True)
for i in df2.columns:
    if i[10:] not in X_2:
        X_2.append(i[10:])

X_2
df2.columns'''

#Calcular el porcentaje de victorias, perdidas y empates. Y quitar el absoluto de estos
letras = ['A','B']
caracteristicas = ['Wins','Losses','Draws']
caracteristicas_2 = ['Body','Head','Leg','Clinch','Distance','Ground']
#'Sig_Str_Landed', 'Sig_Str_Attempted'
#'Totals_Str_Landed', 'Totals_Str_Attempted'
for l in letras:
    for c in caracteristicas:
        df[f'Fighter_{l}_Percentage_{c}'] = np.where(df[f'Fighter_{l}_Total_Fights'] != 0, 
                                           df[f'Fighter_{l}_{c}']+1 / df[f'Fighter_{l}_Total_Fights']+1, -1)
                                                  
        df.drop(columns=[f'Fighter_{l}_{c}'], inplace=True)
    for c2 in caracteristicas_2:
        df[f'Fighter_{l}_Sig_Str_Landed/Attempted_{c2}'] = np.where(df[f'Fighter_{l}_Sig_Str_Attempted_{c2}'] != 0, 
                                           df[f'Fighter_{l}_Sig_Str_Landed_{c2}']+1 / df[f'Fighter_{l}_Sig_Str_Attempted_{c2}']+1, 0)
        df.drop(columns=[f'Fighter_{l}_Sig_Str_Landed_{c2}'], inplace=True)
        df.drop(columns=[f'Fighter_{l}_Sig_Str_Attempted_{c2}'], inplace=True)

    df[f'Fighter_{l}_Sig_Str_Landed/Attempted_Global'] = np.where(df[f'Fighter_{l}_Sig_Str_Attempted'] != 0, 
                                           df[f'Fighter_{l}_Sig_Str_Landed']+1 / df[f'Fighter_{l}_Sig_Str_Attempted']+1, 0) #Le sumo uno a cada uno para aplicar suavizado, aunque en este caso no se si haria falta
    df.drop(columns=[f'Fighter_{l}_Sig_Str_Landed'], inplace=True)
    df.drop(columns=[f'Fighter_{l}_Sig_Str_Attempted'], inplace=True)

    '''df[f'Fighter_{l}_Totals_Str_Landed/Attempted'] = np.where(df[f'Fighter_{l}_Totals_Str_Attempted'] != 0, 
                                           df[f'Fighter_{l}_Totals_Str_Landed'] / df[f'Fighter_{l}_Totals_Str_Attempted']+1, -1)
    df.drop(columns=[f'Fighter_{l}_Totals_Str_Landed'], inplace=True)
    df.drop(columns=[f'Fighter_{l}_Totals_Str_Attempted'], inplace=True)'''

#Quitamos donde debutan ambos
features = df.drop(columns=['Fighter_A_Is_Debut', 'Fighter_B_Is_Debut','Title_Bout','Weight_Class']).columns.tolist()
features_2 = []
for f in features:
    if f[10:] not in features_2:
        features_2.append(f[10:])

print(features_2)
for feat in features_2:
    col_a = f"Fighter_A_{feat}"
    col_b = f"Fighter_B_{feat}"
    ratio_col = f"A/B_{feat}"
    #Probé con la diferencia pero el ratio funciona mejor
    # Evitar divisiones por 0 o valores faltantes
    df[ratio_col] = np.where(df[col_b] != 0, df[col_a] / df[col_b], -1)
# Opcional: reemplazar NaN o inf
#df.replace([np.inf, -np.inf], np.nan, inplace=True)

#df.fillna(0, inplace=True)
df.filter(like="Fighter_A").columns


['Totals_KD', 'Totals_Rev', 'Totals_Sub_att', 'Totals_Td_Pct', 'Totals_Str_Landed', 'Totals_Str_Attempted', 'Totals_Ctrl_Sec', 'Total_Fights', 'Win_Streak', 'Lose_Streak', 'Experience_Years', 'Days_Since_Last_Fight', 'Percentage_Wins', 'Percentage_Losses', 'Percentage_Draws', 'Sig_Str_Landed/Attempted_Body', 'Sig_Str_Landed/Attempted_Head', 'Sig_Str_Landed/Attempted_Leg', 'Sig_Str_Landed/Attempted_Clinch', 'Sig_Str_Landed/Attempted_Distance', 'Sig_Str_Landed/Attempted_Ground', 'Sig_Str_Landed/Attempted_Global']


Index(['Fighter_A_Totals_KD', 'Fighter_A_Totals_Rev',
       'Fighter_A_Totals_Sub_att', 'Fighter_A_Totals_Td_Pct',
       'Fighter_A_Totals_Str_Landed', 'Fighter_A_Totals_Str_Attempted',
       'Fighter_A_Totals_Ctrl_Sec', 'Fighter_A_Total_Fights',
       'Fighter_A_Win_Streak', 'Fighter_A_Lose_Streak',
       'Fighter_A_Experience_Years', 'Fighter_A_Days_Since_Last_Fight',
       'Fighter_A_Is_Debut', 'Fighter_A_Percentage_Wins',
       'Fighter_A_Percentage_Losses', 'Fighter_A_Percentage_Draws',
       'Fighter_A_Sig_Str_Landed/Attempted_Body',
       'Fighter_A_Sig_Str_Landed/Attempted_Head',
       'Fighter_A_Sig_Str_Landed/Attempted_Leg',
       'Fighter_A_Sig_Str_Landed/Attempted_Clinch',
       'Fighter_A_Sig_Str_Landed/Attempted_Distance',
       'Fighter_A_Sig_Str_Landed/Attempted_Ground',
       'Fighter_A_Sig_Str_Landed/Attempted_Global'],
      dtype='object')

In [63]:
#df_d = df.filter(like="Diff_").copy()

df_r = df.filter(like="A/B_").copy()



df_r.drop(['A/B_Totals_Sub_att','A/B_Totals_KD','A/B_Lose_Streak','A/B_Totals_Rev'],inplace=True,axis=1)

'''X_train = df_r.iloc[:5000]
X_val = df_r.iloc[5000:]
y_train = y.iloc[:5000]
y_val = y.iloc[5000:]
y.shape
df_r'''

'X_train = df_r.iloc[:5000]\nX_val = df_r.iloc[5000:]\ny_train = y.iloc[:5000]\ny_val = y.iloc[5000:]\ny.shape\ndf_r'

In [ ]:
'''ufc_weight_classes = {
    "Flyweight": 125,
    "Bantamweight": 135,
    "Featherweight": 145,
    "Lightweight": 155,
    "Welterweight": 170,
    "Middleweight": 185,
    "Light Heavyweight": 205,
    "Heavyweight": 265,
    "Women's Strawweight": 115,
    "Women's Flyweight": 125,
    "Women's Bantamweight": 135,
    "Women's Featherweight": 145,
    "Catch Weight": None,  # peso acordado entre peleadores, sin límite fijo
    "Other": None  # categoría fuera de las divisiones estándar
}
df_r['Weight_lbs'] = df['Weight_Class'].map(ufc_weight_classes)
df_r.dropna(subset=['Weight_lbs'],inplace=True)

#df[df['Weight_Class'] == 'Catch Weight']
#df[df['Weight_Class'] == 'Other']
df_r.tail(50)'''

In [65]:
def calcular_sample_weights(df):
    N_PELEAS = df.shape[0]
    time_index = np.arange(N_PELEAS) 
    normalized_time = time_index / (N_PELEAS - 1)
    gamma = 4 
    sample_weights = np.exp(gamma * normalized_time)
    return sample_weights

In [69]:
#df_r.drop(['Weight_Class'],inplace=True, axis=1)
#df2.drop(['Weight_Class'], axis=1,inplace=True)
y

17      1
21      1
22      1
25      1
27      0
       ..
7430    1
7431    0
7432    0
7433    0
7434    0
Name: Winner_A, Length: 6936, dtype: int64

In [25]:
def objective(trial,X,y):
    param = {
            'n_estimators': trial.suggest_int('n_estimators', 400, 1000),
            'max_depth': trial.suggest_int('max_depth', 7, 20),
            'min_samples_leaf': trial.suggest_int('min_samples_leaf', 20, 40),
            'min_samples_split': trial.suggest_int('min_samples_split', 20,40),
            'max_features': trial.suggest_float('max_features', 0.3, 0.6 ),
            'criterion': trial.suggest_categorical('criterion', ['gini', 'entropy']),
            'class_weight': trial.suggest_categorical('class_weight', ['balanced']),
            'max_samples': trial.suggest_float('max_samples', 0.7, 0.9, step=0.1)
        #bootstrap está true por defecto
        }
        
    model_base = RandomForestClassifier(**param, random_state=42, n_jobs=-1)
    tscv = TimeSeriesSplit(n_splits=10)
    sw = calcular_sample_weights(X)
    fold_scores = []
    for train_index, test_index in tscv.split(X):
        # A. División de Datos: Usamos .iloc para obtener los subconjuntos
        X_train, X_test = X.iloc[train_index], X.iloc[test_index]
        y_train, y_test = y.iloc[train_index], y.iloc[test_index]
        
        # B. División de Pesos: Obtenemos los pesos correspondientes al TRAINING set
        sw_train = sw[train_index]
        
        # C. Clonar y Entrenar
        # Usamos clone() para asegurar que cada fold usa una instancia nueva
        model = clone(model_base) 
        
        # 🚩 Aplicamos el peso directamente al método .fit()
        model.fit(X_train, y_train, sample_weight=sw_train) 
        
        # D. Evaluar (usando f1_weighted, como en tu código original)
        y_pred = model.predict(X_test)
        score = f1_score(y_test, y_pred, average='weighted')
        fold_scores.append(score)
        
    
    return np.mean(fold_scores)

study = optuna.create_study(direction='maximize')  # 'maximize' para maximizar la precisión

# Ejecutar la optimización de hiperparámetros
study.optimize(lambda trial: objective(trial, df_r, y), n_trials=50)

[I 2025-11-08 17:37:08,940] A new study created in memory with name: no-name-13b61ead-b85c-4e44-8845-ec371e0a119c
[I 2025-11-08 17:37:35,188] Trial 0 finished with value: 0.5507426664369606 and parameters: {'n_estimators': 823, 'max_depth': 10, 'min_samples_leaf': 38, 'min_samples_split': 20, 'max_features': 0.5817533246491247, 'criterion': 'entropy', 'class_weight': 'balanced', 'max_samples': 0.7999999999999999}. Best is trial 0 with value: 0.5507426664369606.
[I 2025-11-08 17:37:58,253] Trial 1 finished with value: 0.5489119369316917 and parameters: {'n_estimators': 722, 'max_depth': 7, 'min_samples_leaf': 20, 'min_samples_split': 40, 'max_features': 0.597838344227296, 'criterion': 'entropy', 'class_weight': 'balanced', 'max_samples': 0.7}. Best is trial 0 with value: 0.5507426664369606.
[I 2025-11-08 17:38:23,652] Trial 2 finished with value: 0.5512633046727453 and parameters: {'n_estimators': 920, 'max_depth': 11, 'min_samples_leaf': 36, 'min_samples_split': 24, 'max_features': 0.3

KeyboardInterrupt: 

In [29]:
from xgboost import XGBClassifier
def objective(trial,X,y):
    param = {
        # 1. Parámetros del Árbol (Similares a 'max_depth' y 'n_estimators')
        'n_estimators': trial.suggest_int('n_estimators', 400, 1200), # Número de etapas de boosting (árboles)
        'max_depth': trial.suggest_int('max_depth', 4, 8),           # Profundidad máxima de cada árbol
    
        # 2. Regularización y Tasa de Aprendizaje (Específicos de Boosting)
        'learning_rate': trial.suggest_float('learning_rate', 0.001, 0.3, log=True), # Tasa de aprendizaje
        'gamma': trial.suggest_float('gamma', 0.0, 0.7),                           # Mínima pérdida de reducción para hacer una partición
        'lambda': trial.suggest_float('lambda', 0.1, 2.0, log=True),              # Regularización L2 (similar a 'class_weight' o 'min_samples_leaf' pero en pérdida)
        'alpha': trial.suggest_float('alpha', 0.05, 1.0, log=True),               # Regularización L1
    
        # 3. Muestreo (Similares a 'max_features' y 'max_samples')
        'subsample': trial.suggest_float('subsample', 0.75, 0.95),                  # Fracción de muestras a usar por cada árbol (similar a 'max_samples')
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.3, 0.8),    # Fracción de características a usar por cada árbol (similar a 'max_features')
    
        # 4. Parámetros de la Partición (Sustituyen a 'min_samples_leaf' y 'min_samples_split')
        # Estos controlan la complejidad de la hoja directamente.
        'min_child_weight': trial.suggest_int('min_child_weight', 10, 60) # Peso mínimo de la instancia en un nodo hijo. Valores mayores son más conservadores.
    }
        
    model_base = XGBClassifier(**param, random_state=42, n_jobs=-1)
    tscv = TimeSeriesSplit(n_splits=10)
    sw = calcular_sample_weights(X)
    fold_scores = []
    t_scores = []
    for train_index, test_index in tscv.split(X):
        # A. División de Datos: Usamos .iloc para obtener los subconjuntos
        X_train, X_test = X.iloc[train_index], X.iloc[test_index]
        y_train, y_test = y.iloc[train_index], y.iloc[test_index]
        
        # B. División de Pesos: Obtenemos los pesos correspondientes al TRAINING set
        sw_train = sw[train_index]
        
        # C. Clonar y Entrenar
        # Usamos clone() para asegurar que cada fold usa una instancia nueva
        model = clone(model_base) 
        
        # 🚩 Aplicamos el peso directamente al método .fit()
        model.fit(X_train, y_train, sample_weight=sw_train) 
        train_score = model.score(X_train,y_train)
        t_scores.append(train_score)
        # D. Evaluar (usando f1_weighted, como en tu código original)
        y_pred = model.predict(X_test)
        score = f1_score(y_test, y_pred, average='weighted')
        fold_scores.append(score)
        
    print(np.mean(t_scores))
    return np.mean(fold_scores)

study = optuna.create_study(direction='maximize')  # 'maximize' para maximizar la precisión

# Ejecutar la optimización de hiperparámetros
study.optimize(lambda trial: objective(trial, df_r, y), n_trials=50)

[I 2025-11-09 21:12:25,465] A new study created in memory with name: no-name-d284b10e-d7ca-426a-b049-9c86278d839d
[I 2025-11-09 21:12:30,844] Trial 0 finished with value: 0.5202944846062245 and parameters: {'n_estimators': 948, 'max_depth': 4, 'learning_rate': 0.062361851656193616, 'gamma': 0.6632374459479389, 'lambda': 0.2751797511299414, 'alpha': 0.9431923604869855, 'subsample': 0.766916700186319, 'colsample_bytree': 0.3883159369765365, 'min_child_weight': 39}. Best is trial 0 with value: 0.5202944846062245.


0.8028591598808319


[I 2025-11-09 21:12:37,470] Trial 1 finished with value: 0.5313911248522007 and parameters: {'n_estimators': 607, 'max_depth': 8, 'learning_rate': 0.029720984502086153, 'gamma': 0.3403226923248932, 'lambda': 0.43289821077611235, 'alpha': 0.4669189786944745, 'subsample': 0.8412615916262383, 'colsample_bytree': 0.7404663241227505, 'min_child_weight': 24}. Best is trial 1 with value: 0.5313911248522007.


0.8465807171343315


[I 2025-11-09 21:12:44,039] Trial 2 finished with value: 0.517325880231067 and parameters: {'n_estimators': 1102, 'max_depth': 4, 'learning_rate': 0.002184744094929757, 'gamma': 0.5127500992606879, 'lambda': 0.281213598655282, 'alpha': 0.1486191593176366, 'subsample': 0.8881002376870568, 'colsample_bytree': 0.5637431866828584, 'min_child_weight': 42}. Best is trial 1 with value: 0.5313911248522007.


...

0.8554990783099559


[I 2025-11-09 21:17:54,884] Trial 48 finished with value: 0.5217310607345527 and parameters: {'n_estimators': 706, 'max_depth': 6, 'learning_rate': 0.003568636232395747, 'gamma': 0.034761193985904514, 'lambda': 0.39683610353913346, 'alpha': 0.15563643117972392, 'subsample': 0.8431093772039394, 'colsample_bytree': 0.7976291342262039, 'min_child_weight': 33}. Best is trial 21 with value: 0.5391459586988046.


0.7188449305789485


[I 2025-11-09 21:18:00,691] Trial 49 finished with value: 0.5297258100945949 and parameters: {'n_estimators': 888, 'max_depth': 5, 'learning_rate': 0.014483534995724733, 'gamma': 0.000982398593391554, 'lambda': 1.1614171324995382, 'alpha': 0.18774269580056008, 'subsample': 0.889000199686697, 'colsample_bytree': 0.4821549525524671, 'min_child_weight': 38}. Best is trial 21 with value: 0.5391459586988046.


0.765072484524931


In [91]:
import optuna
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score

def objective(trial, X, y):
    """
    Función objetivo de Optuna para la Regresión Logística (Corregida).
    """
    
    # C: Inverso de la fuerza de regularización.
    C = trial.suggest_float('C', 1e-5, 1e2, log=True)
    
    # Penalty: Tipo de regularización.
    # ¡CORRECCIÓN! Usamos el objeto None, no la cadena 'none'.
    penalty = trial.suggest_categorical('penalty', ['l1', 'l2', 'elasticnet', None])
    
    # Solvers
    all_solvers = ['lbfgs', 'liblinear', 'newton-cg', 'sag', 'saga']
    solver = trial.suggest_categorical('solver', all_solvers)
    
    l1_ratio = None
    
    # --- Manejo de Incompatibilidad Penalty/Solver ---
    
    if penalty == 'l1' and solver not in ['liblinear', 'saga']:
        # Solo 'liblinear' y 'saga' soportan L1
        raise optuna.exceptions.TrialPruned()
        
    elif penalty == 'l2' and solver == 'liblinear':
        # 'liblinear' soporta L2, pero puedes excluirlo si quieres.
        pass 

    elif penalty == 'elasticnet':
        # Solo 'saga' soporta 'elasticnet'
        if solver != 'saga':
            raise optuna.exceptions.TrialPruned()
        l1_ratio = trial.suggest_float('l1_ratio', 0.0, 1.0)
        
    # ¡CORRECCIÓN! Comprobamos con 'is None'
    elif penalty is None and solver == 'liblinear':
        # 'liblinear' no soporta 'none' (penalty=None).
        raise optuna.exceptions.TrialPruned()
    
    # --- Construcción y Evaluación del Modelo ---
    
    param = {
        'C': C,
        'penalty': penalty,
        'solver': solver,
        'l1_ratio': l1_ratio, 
        'class_weight': trial.suggest_categorical('class_weight', [None, 'balanced']),
        'max_iter': trial.suggest_int('max_iter', 100, 1000, step=100),
        'random_state': 42,
        'n_jobs': -1 # n_jobs para LogisticRegression
    }
    
    model = LogisticRegression(**param)

    # Evaluar con 5-fold cross-validation
    # Usamos las variables 'X' e 'y' pasadas a la función
    scores = cross_validate(model, X, y, cv=5, n_jobs=-1, scoring='f1_weighted', return_train_score=True)
    print(scores["train_score"].mean())
    return scores["test_score"].mean()

study = optuna.create_study(direction='maximize') 
print("Iniciando la optimización...")
study.optimize(lambda trial: objective(trial, df_r, y), n_trials=50)
print(f"Mejor trial: {study.best_trial.value}")
print(f"Mejores parámetros: {study.best_params}")

[I 2025-11-10 18:35:29,723] A new study created in memory with name: no-name-85912000-23da-459a-af1c-57b322064746
[I 2025-11-10 18:35:29,723] Trial 0 pruned. 
[I 2025-11-10 18:35:29,723] Trial 1 pruned. 
[I 2025-11-10 18:35:29,723] Trial 2 pruned. 
[I 2025-11-10 18:35:29,736] Trial 3 pruned. 


Iniciando la optimización...


[I 2025-11-10 18:35:33,390] Trial 4 finished with value: 0.5334007555351689 and parameters: {'C': 0.0002843260115268077, 'penalty': 'l2', 'solver': 'sag', 'class_weight': 'balanced', 'max_iter': 500}. Best is trial 4 with value: 0.5334007555351689.


0.5443413997896674


[W 2025-11-10 18:35:36,566] Trial 5 failed with parameters: {'C': 0.0011248367311389555, 'penalty': 'elasticnet', 'solver': 'saga', 'l1_ratio': 0.15448279521500785, 'class_weight': 'balanced', 'max_iter': 500} because of the following error: KeyboardInterrupt().
Traceback (most recent call last):
  File "C:\Users\Lluc\anaconda3\envs\ml\lib\site-packages\joblib\parallel.py", line 1682, in _get_outputs
    yield from self._retrieve()
  File "C:\Users\Lluc\anaconda3\envs\ml\lib\site-packages\joblib\parallel.py", line 1800, in _retrieve
    time.sleep(0.01)
KeyboardInterrupt

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "C:\Users\Lluc\anaconda3\envs\ml\lib\site-packages\optuna\study\_optimize.py", line 201, in _run_trial
    value_or_values = func(trial)
  File "C:\Users\Lluc\AppData\Local\Temp\ipykernel_700\3857266088.py", line 67, in <lambda>
    study.optimize(lambda trial: objective(trial, df_r, y), n_trials=50)
  File "

KeyboardInterrupt: 

In [ ]:


kernel = trial.suggest_categorical('kernel', ['rbf', 'poly','linear'])

    # 2. Parámetro de Regularización Común (C)
    # Es crucial y se aplica a todos los kernels.
    C = trial.suggest_float('C', 0.01, 10.0, log=True)
    
    # Parámetro común para el manejo del desbalanceo
    class_weight = trial.suggest_categorical('class_weight', [None, 'balanced'])

    # 3. Parámetros Condicionales según el Kernel
    if kernel == 'linear':
        # Kernel Lineal: Solo necesita C
        svc_params = {
            'C': C,
            'kernel': kernel,
            'class_weight': class_weight,
            # No hay gamma ni degree que optimizar
        }
        
    elif kernel == 'rbf':
        # Kernel RBF: Necesita gamma
        gamma = trial.suggest_float('gamma', 1e-4, 1.0, log=True)
        svc_params = {
            'C': C,
            'kernel': kernel,
            'gamma': gamma,
            'class_weight': class_weight,
        }
        
    elif kernel == 'poly':
        # Kernel Polinomial: Necesita degree, gamma y coef0
        degree = trial.suggest_int('degree', 2, 4) # Grados 2, 3 o 4
        gamma = trial.suggest_float('gamma', 1e-4, 1.0, log=True)
        coef0 = trial.suggest_float('coef0', 0.0, 10.0)
        svc_params = {
            'C': C,
            'kernel': kernel,
            'degree': degree,
            'gamma': gamma,
            'coef0': coef0,
            'class_weight': class_weight,
        }

In [105]:
#SVM, tarda una barbaridad
tscv = TimeSeriesSplit(n_splits=10)
def objective(trial,X,y):
    # 1. Elección del Kernel
    kernel = trial.suggest_categorical('kernel', ['linear', 'rbf', 'poly'])

    # 2. Parámetros Comunes
    C = trial.suggest_categorical('C', [0.01, 1, 10, 100])
    class_weight = trial.suggest_categorical('class_weight', [None, 'balanced'])

    # 3. Definición de GAMMA (UNA SOLA VEZ) con todas las opciones
    # Incluye las opciones de RBF y la opción 'scale' necesaria para POLY/RBF
    # NOTA: Para RBF, puedes necesitar 1e-4 o 0.01. Aquí asumimos que quieres 'scale', 0.01 y 1.
    gamma_options = [0.01, 'scale', 1] 
    gamma = trial.suggest_categorical('gamma', gamma_options) 

    # Diccionario base para SVC
    svc_params = {
        'C': C,
        'kernel': kernel,
        'class_weight': class_weight,
    }
    
    # 4. Parámetros Condicionales (Asignación)
    if kernel == 'rbf':
        # Ya tiene C, kernel, class_weight. Solo añade gamma.
        svc_params['gamma'] = gamma
        
    elif kernel == 'poly':
        # Necesita degree, coef0 y gamma
        degree = trial.suggest_int('degree', 2, 3) 
        coef0 = trial.suggest_categorical('coef0', [0.0, 1.0])
        
        svc_params['degree'] = degree
        svc_params['gamma'] = gamma
        svc_params['coef0'] = coef0
    
    model = SVC(**svc_params, random_state=42)
    scores = cross_validate(model, X, y, cv=tscv, n_jobs=-1, scoring='f1_weighted', return_train_score=True)
    print(scores["train_score"].mean())
    return scores["test_score"].mean()
    
study = optuna.create_study(direction='maximize')  # 'maximize' para maximizar la precisión
study.optimize(lambda trial: objective(trial, df_r, y), n_trials=20)

[I 2025-11-10 18:59:30,073] A new study created in memory with name: no-name-fb9e677b-28ac-40f3-89f8-87a7e9487d3a
[W 2025-11-10 19:02:30,330] Trial 0 failed with parameters: {'kernel': 'poly', 'C': 1, 'class_weight': None, 'gamma': 1, 'degree': 2, 'coef0': 1.0} because of the following error: KeyboardInterrupt().
Traceback (most recent call last):
  File "C:\Users\Lluc\anaconda3\envs\ml\lib\site-packages\optuna\study\_optimize.py", line 201, in _run_trial
    value_or_values = func(trial)
  File "C:\Users\Lluc\AppData\Local\Temp\ipykernel_700\2102840034.py", line 44, in <lambda>
    study.optimize(lambda trial: objective(trial, df_r, y), n_trials=20)
  File "C:\Users\Lluc\AppData\Local\Temp\ipykernel_700\2102840034.py", line 39, in objective
    scores = cross_validate(model, X, y, cv=tscv, n_jobs=-1, scoring='f1_weighted', return_train_score=True)
  File "C:\Users\Lluc\anaconda3\envs\ml\lib\site-packages\sklearn\utils\_param_validation.py", line 218, in wrapper
    return func(*args, 

KeyboardInterrupt: 

In [ ]:
def objective(trial,X,y):
    # Definir los hiperparámetros que queremos optimizar
    param = {
        'learning_rate': trial.suggest_float('learning_rate', 1e-4, 1e-1, log=True),
        'max_depth': trial.suggest_int('max_depth', 3, 30),
        'min_child_weight': trial.suggest_int('min_child_weight', 4, 10),
        'subsample': trial.suggest_float('subsample', 0.6, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.6, 1.0),
        'gamma': trial.suggest_float('gamma', 1e-4, 1e-1, log=True),
        'n_estimators': trial.suggest_int('n_estimators', 100, 500),
        'reg_alpha': trial.suggest_float('reg_alpha', 1e-4, 2, log=True),
        'reg_lambda': trial.suggest_float('reg_lambda', 1e-4, 1, log=True),
        'scale_pos_weight': trial.suggest_float('scale_pos_weight', 1, 2, log=True),
        # you can also add 'nthread' or 'verbosity' here if desired
    }
    
    model = Pipeline(steps=[
    #('preprocessor', preprocessor),
    ('classifier', xgb.XGBClassifier(**param, random_state=42, n_jobs=-1))
    ])
    
    scores = cross_val_score(model, X, y, cv=10, n_jobs=-1, scoring='roc_auc')
    
    return scores.mean()  # Esta es la métrica que Optuna va a intentar maximizar

study = optuna.create_study(direction='maximize')  # 'maximize' para maximizar la precisión

# Ejecutar la optimización de hiperparámetros
study.optimize(lambda trial: objective(trial, df_r, y), n_trials=50)

In [ ]:
best_params = study.best_params

# Crear el modelo final con los mejores hiperparámetros
final_model = RandomForestClassifier(**best_params)

# Entrenar el modelo final
final_model.fit(X_train, y_train)

In [ ]:
'''c_features = ['Weight_Class']
other_columns = df_r.columns.tolist()
other_columns.remove(c_features[0])
preprocessor = ColumnTransformer(
    transformers=[
        #('num', StandardScaler(), numeric_features),  # Scale numeric features
        ('cat', OneHotEncoder(), c_features),  # Apply OneHotEncoder to categorical features
        ('other', 'passthrough', other_columns)
    ])
final_model = Pipeline(steps=[
    #('preprocessor', preprocessor),
    ('classifier', RandomForestClassifier(random_state=seed))
    ])
#print( 'Weight_Class' in c_features)'''
#df_r.drop(['A/B_Win_Streak'],inplace=True, axis=1)


#X_train, X_val, y_train, y_val = train_test_split(df_r[1000:], y[1000:], test_size=0.2, random_state=2)
#final_model.fit(X_train, y_train)


params = {'n_estimators': 430, 'max_depth': 21, 'min_samples_split': 11, 'min_samples_leaf': 7, 'max_features': 0.632268301082106, 'criterion': 'gini', 'class_weight': None}
scores = []
seeds= range(10)
for seed in seeds:
    model = RandomForestClassifier(**params, random_state=seed)
    cv_scores = cross_val_score(model, df_r, y, cv=10, n_jobs=-1)
    scores.append(cv_scores.mean())
#y_pred = final_model.predict(X_val)
#accuracy = accuracy_score(y_val, y_pred)
print('Media: ',np.mean(scores))
print('SD: ',np.std(scores))
#0,5611 quitando primeras 1000 peleas
#0,5685 con todas las peleas, pero debería predecir de los últimos años
#0,573 con wins los ratio poniendo que si division por 0 de -1, en lugar de antes que estaba 0
# 0,569 quitandole el suavizado a wins los ratio
# 0,575 volviendo a poner el suavizado y poniendo -1 div por 0 en landed/attempted
# Empeora quitando el suavizado a landed/attempted
# Empeora si division por 0 --> -1 en landed/attempted global

# 0,566 con ratioA/B -1 sin suavizado
# 0,565 con ratio 0 sin suavizado
# 0,543 con ratio 0 con suavizado
#0,5689 con suavizado y 0 landed/attempted

In [ ]:
lrparam={'C': 0.0007548726745372139, 'penalty': 'l2', 'solver': 'lbfgs', 'class_weight': 'balanced', 'max_iter': 600}
model= LogisticRegression(**lrparam)
#cv_scores = cross_val_score(final_model, df_r, y, cv=10, n_jobs=-1)
#y_pred = final_model.predict(X_val)
#accuracy = accuracy_score(y_val, y_pred)
model.fit(X_train,y_train)
print(model.score(X_train,y_train))
print(model.score(X_val, y_val))
#print('Media: ',np.mean(cv_scores))
#print('SD: ',np.std(cv_scores))


In [71]:
def calcular_sample_weights(df):
    N_PELEAS = df.shape[0]
    time_index = np.arange(N_PELEAS) 
    normalized_time = time_index / (N_PELEAS - 1)
    gamma = 4 
    sample_weights = np.exp(gamma * normalized_time)
    return sample_weights

In [31]:
#import eli5
#from eli5.sklearn import PermutationImportance

final_model = Pipeline(steps=[
    #('preprocessor', preprocessor),
    ('classifier', RandomForestClassifier(random_state=7))
    ])

X_train = df_r.iloc[:5000]
X_val = df_r.iloc[5000:]
y_train = y.iloc[:5000]
y_val = y.iloc[5000:]

params2= {'n_estimators': 383, 'max_depth': 22, 'min_samples_split': 14, 'min_samples_leaf': 17, 'max_features': 0.2620662228323929, 'criterion': 'entropy', 'class_weight': None}
params3 = {'n_estimators': 430, 'max_depth': 10, 'min_samples_split': 10, 'min_samples_leaf': 29, 'max_features': 0.43959840795841465, 'criterion': 'entropy', 'class_weight': None}
params_f1_3={'n_estimators': 631, 'max_depth': 7, 'min_samples_leaf': 30, 'min_samples_split': 15, 'max_features': 0.31620623716837837, 'criterion': 'entropy', 'class_weight': None}
params_f1_4={'n_estimators': 754, 'max_depth': 7, 'min_samples_leaf': 34, 'min_samples_split': 29, 'max_features': 0.36299698057912727, 'criterion': 'entropy', 'class_weight': 'balanced', 'max_samples': 0.6}
params_f1_5={'n_estimators': 610, 'max_depth': 8, 'min_samples_leaf': 40, 'min_samples_split': 24, 'max_features': 0.30952884472934816, 'criterion': 'gini', 'class_weight': 'balanced', 'max_samples': 0.7}
params_tscv={'n_estimators': 448, 'max_depth': 17, 'min_samples_leaf': 20, 'min_samples_split': 35, 'max_features': 0.5108848446793676, 'criterion': 'entropy', 'class_weight': 'balanced', 'max_samples': 0.7999999999999999}
s_train = []
s_test = []
sw = calcular_sample_weights(X_train)
model = RandomForestClassifier(**params_tscv, random_state=42)
model.fit(X_train, y_train,sample_weight=sw)
s1=model.score(X_train,y_train)
s2=model.score(X_val, y_val)

print('Train: ',s1)
print('Test: ',s2)

#perm = PermutationImportance(final_model, random_state=8).fit(X_val, y_val)
#eli5.show_weights(perm, feature_names = X_val.columns.tolist(), top=None) #Hay más feature names por el one hot

#params2 el mejor sin usar tscv ni sample weights
#params3 Train:  0.7056713741313607 Test:  0.5704998879175073
#paramsf1_3 Train:  0.6557946648733467 Test:  0.5691548980049316 MEJOR

# HACIENDO TRAIN HASTA 5000 Y TEST CON LAS FILAS RESTANTES
# Params2: Train:  0.7696 Test:  0.5613963039014374
    # sw con gamma 5 Train:  0.7132 Test:  0.5507186858316222
    # sw con gamma 3 Train:  0.7514 Test:  0.5589322381930185
    # sw con gamma 4 Train:  0.7286 Test:  0.5613963039014374
# params_tscv Train:  0.6782 Test:  0.5564681724845996

Train:  0.6782
Test:  0.5564681724845996


In [89]:
feature_importances = pd.Series(
    model.feature_importances_, 
    index=df_r.columns
).sort_values(ascending=False)

# Mostrar la importancia
print("\nTop 10 Características más Importantes:")
print(feature_importances.head(50))


Top 10 Características más Importantes:
A/B_Percentage_Losses                    0.094800
A/B_Percentage_Wins                      0.086216
A/B_Totals_Str_Landed                    0.066360
A/B_Sig_Str_Landed/Attempted_Ground      0.064711
A/B_Totals_Str_Attempted                 0.059026
A/B_Sig_Str_Landed/Attempted_Body        0.057435
A/B_Sig_Str_Landed/Attempted_Head        0.056821
A/B_Sig_Str_Landed/Attempted_Leg         0.053459
A/B_Days_Since_Last_Fight                0.053340
A/B_Experience_Years                     0.053126
A/B_Sig_Str_Landed/Attempted_Clinch      0.052577
A/B_Totals_Ctrl_Sec                      0.052449
A/B_Sig_Str_Landed/Attempted_Distance    0.050786
A/B_Sig_Str_Landed/Attempted_Global      0.049047
A/B_Totals_Td_Pct                        0.048944
A/B_Percentage_Draws                     0.044723
A/B_Total_Fights                         0.028600
A/B_Win_Streak                           0.027582
dtype: float64


In [ ]:
params_xgb={'learning_rate': 0.0035076049733885656, 'max_depth': 30, 'min_child_weight': 9, 'subsample': 0.6879851114237657, 'colsample_bytree': 0.8977961757743093, 'gamma': 0.06089912781364358, 'n_estimators': 171, 'reg_alpha': 0.017448425104392137, 'reg_lambda': 0.2715753137877096, 'scale_pos_weight': 1.0074766777468596}
model = xgb.XGBClassifier(**params, random_state=seed)
X_train, X_val, y_train, y_val = train_test_split(df_r, y, test_size=0.2, random_state=6)
model.fit(X_train, y_train)
print(model.score(X_train,y_train))
print(model.score(X_val, y_val))

In [ ]:
datos = {'feature':X_val.columns, 'importance': perm.feature_importances_}
importance_df = pd.DataFrame(datos)
None

In [ ]:
params_regresion_logistica = {'C': 0.0011656645858048162, 'penalty': 'l2', 'solver': 'liblinear', 'class_weight': 'balanced', 'max_iter': 100}

In [ ]:
final_model.fit(X,y)
df = pd.read_csv('test_set.csv')
#df = df.iloc[1000:]
ids = df['Fight_ID']
df.drop(['Fighter_A_Name', 'Fighter_B_Name', 'Date', 'Weight_Class',
       'Title_Bout', 'Referee', 'Location', 'Country', 'Continent', 'Season', 'Fight_ID'], axis=1, inplace=True)
predictions = model.predict(df)
results = pd.DataFrame({
    'Fight_ID': ids,  # o X_test.index si no tienes una columna 'id'
    'Winner': predictions
})

results.to_csv('submission.csv', index=False)

print("Archivo 'submission.csv' creado exitosamente.")                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

In [73]:
def preprocesar():
    df = pd.read_csv('test_set.csv')
    ids = df['Fight_ID']
    df.drop(['Fighter_A_Name', 'Fighter_B_Name', 'Date',
             'Referee', 'Location', 'Country', 'Continent', 'Season','Fight_ID'], axis=1, inplace=True)
    
    letras = ['A','B']
    caracteristicas = ['Wins','Losses','Draws']
    caracteristicas_2 = ['Body','Head','Leg','Clinch','Distance','Ground']
    
    for l in letras:
        for c in caracteristicas:
            df[f'Fighter_{l}_Percentage_{c}'] = np.where(df[f'Fighter_{l}_Total_Fights'] != 0, 
                                               df[f'Fighter_{l}_{c}']+1 / df[f'Fighter_{l}_Total_Fights']+1, -1)
                                                      
            df.drop(columns=[f'Fighter_{l}_{c}'], inplace=True)
        for c2 in caracteristicas_2:
            df[f'Fighter_{l}_Sig_Str_Landed/Attempted_{c2}'] = np.where(df[f'Fighter_{l}_Sig_Str_Attempted_{c2}'] != 0, 
                                               df[f'Fighter_{l}_Sig_Str_Landed_{c2}']+1 / df[f'Fighter_{l}_Sig_Str_Attempted_{c2}']+1, 0)
            df.drop(columns=[f'Fighter_{l}_Sig_Str_Landed_{c2}'], inplace=True)
            df.drop(columns=[f'Fighter_{l}_Sig_Str_Attempted_{c2}'], inplace=True)
    
        df[f'Fighter_{l}_Sig_Str_Landed/Attempted_Global'] = np.where(df[f'Fighter_{l}_Sig_Str_Attempted'] != 0, 
                                               df[f'Fighter_{l}_Sig_Str_Landed']+1 / df[f'Fighter_{l}_Sig_Str_Attempted']+1, 0) #Le sumo uno a cada uno para aplicar suavizado, aunque en este caso no se si haria falta
        df.drop(columns=[f'Fighter_{l}_Sig_Str_Landed'], inplace=True)
        df.drop(columns=[f'Fighter_{l}_Sig_Str_Attempted'], inplace=True)
    
        '''df[f'Fighter_{l}_Totals_Str_Landed/Attempted'] = np.where(df[f'Fighter_{l}_Totals_Str_Attempted'] != 0, 
                                               df[f'Fighter_{l}_Totals_Str_Landed'] / df[f'Fighter_{l}_Totals_Str_Attempted']+1, -1)
        df.drop(columns=[f'Fighter_{l}_Totals_Str_Landed'], inplace=True)
        df.drop(columns=[f'Fighter_{l}_Totals_Str_Attempted'], inplace=True)'''
    
    
    features = df.drop(columns=['Fighter_A_Is_Debut', 'Fighter_B_Is_Debut','Title_Bout','Weight_Class']).columns.tolist()
    features_2 = []
    for f in features:
        if f[10:] not in features_2:
            features_2.append(f[10:])
    
    print(features_2)
    for feat in features_2:
        col_a = f"Fighter_A_{feat}"
        col_b = f"Fighter_B_{feat}"
        ratio_col = f"A/B_{feat}"
        #Probé con la diferencia pero el ratio funciona mejor
        # Evitar divisiones por 0 o valores faltantes
        df[ratio_col] = np.where(df[col_b] != 0, df[col_a] / df[col_b], -1)
    # Opcional: reemplazar NaN o inf
    #df.replace([np.inf, -np.inf], np.nan, inplace=True)
    
    #df.fillna(0, inplace=True)
    
    df_r = df.filter(like="A/B_").copy()
    
    
    
    df_r.drop(['A/B_Totals_Sub_att','A/B_Totals_KD','A/B_Lose_Streak','A/B_Totals_Rev'],inplace=True,axis=1)
    return df_r, ids

In [75]:
df_test, ids = preprocesar()

['Totals_KD', 'Totals_Rev', 'Totals_Sub_att', 'Totals_Td_Pct', 'Totals_Str_Landed', 'Totals_Str_Attempted', 'Totals_Ctrl_Sec', 'Total_Fights', 'Win_Streak', 'Lose_Streak', 'Experience_Years', 'Days_Since_Last_Fight', 'Percentage_Wins', 'Percentage_Losses', 'Percentage_Draws', 'Sig_Str_Landed/Attempted_Body', 'Sig_Str_Landed/Attempted_Head', 'Sig_Str_Landed/Attempted_Leg', 'Sig_Str_Landed/Attempted_Clinch', 'Sig_Str_Landed/Attempted_Distance', 'Sig_Str_Landed/Attempted_Ground', 'Sig_Str_Landed/Attempted_Global']


In [39]:
df_test.columns

Index(['A/B_Totals_Td_Pct', 'A/B_Totals_Str_Landed',
       'A/B_Totals_Str_Attempted', 'A/B_Totals_Ctrl_Sec', 'A/B_Total_Fights',
       'A/B_Win_Streak', 'A/B_Experience_Years', 'A/B_Days_Since_Last_Fight',
       'A/B_Percentage_Wins', 'A/B_Percentage_Losses', 'A/B_Percentage_Draws',
       'A/B_Sig_Str_Landed/Attempted_Body',
       'A/B_Sig_Str_Landed/Attempted_Head', 'A/B_Sig_Str_Landed/Attempted_Leg',
       'A/B_Sig_Str_Landed/Attempted_Clinch',
       'A/B_Sig_Str_Landed/Attempted_Distance',
       'A/B_Sig_Str_Landed/Attempted_Ground',
       'A/B_Sig_Str_Landed/Attempted_Global'],
      dtype='object')

In [83]:
params = {'n_estimators': 430, 'max_depth': 21, 'min_samples_split': 11, 'min_samples_leaf': 7, 'max_features': 0.632268301082106, 'criterion': 'gini', 'class_weight': None}
params_xgb = {'n_estimators': 756, 'max_depth': 5, 'learning_rate': 0.008832788498438778, 'gamma': 0.0005727040575858942, 'lambda': 1.0362951959084774, 'alpha': 0.15560195974791888, 'subsample': 0.9133887655034906, 'colsample_bytree': 0.7997915953852921, 'min_child_weight': 10}
params_tscv={'n_estimators': 448, 'max_depth': 17, 'min_samples_leaf': 20, 'min_samples_split': 35, 'max_features': 0.5108848446793676, 'criterion': 'entropy', 'class_weight': 'balanced', 'max_samples': 0.7999999999999999}
model = RandomForestClassifier(**params_tscv, random_state=42)
model.fit(df_r,y,sample_weight=sample_weights)
predictions = model.predict(df_test)
results = pd.DataFrame({
    'Fight_ID': ids,  # o X_test.index si no tienes una columna 'id'
    'Winner': predictions
})

results.to_csv('submission.csv', index=False)
#He vuelto a poner gamma = 5, porqué dio mejor resultado en el leaderboard, última submission tenía gamma = 5.5

In [ ]:
sample_weights[4000]

In [79]:
# --- Asunciones de tu entorno ---
# X: DataFrame/Numpy array de características
# y: Serie/Numpy array de la variable objetivo
# N_PELEAS = 7500 (o el número total de filas en tus datos)

# 1. Obtener el índice (antigüedad relativa)
N_PELEAS = df_r.shape[0]
# Crea un array que va de 0 a N-1. 
# 0 es la pelea más antigua, N-1 es la más reciente.
time_index = np.arange(N_PELEAS) 

# 2. Normalizar el tiempo (escala de 0 a 1)
# 0 sigue siendo la más antigua, 1 es la más reciente.
normalized_time = time_index / (N_PELEAS - 1)

# 3. Calcular el decaimiento. Queremos que el peso sea alto cuando el tiempo es alto.
# Usamos una función exponencial creciente o simplemente invertimos la base del exponente.
# Factor de Crecimiento (gamma): Un valor más alto penaliza más al pasado.
gamma = 5 

# Fórmula: weight = e^(gamma * normalized_time)
# Ejemplo con gamma=5: 
# Pelea Antigua (t=0) -> weight = e^0 = 1
# Pelea Reciente (t=1) -> weight = e^5 ≈ 148
sample_weights = np.exp(gamma * normalized_time)

# Opcional: Normalizar los pesos para que sumen el número de muestras (si el solver lo requiere)
# sample_weights = sample_weights / sample_weights.sum() * N_PELEAS

In [81]:
sample_weights

array([  1.        ,   1.00072124,   1.001443  , ..., 148.19930733,
       148.30619467, 148.4131591 ], shape=(6936,))

In [ ]:
import sklearn
print(sklearn.__version__)

In [85]:
df_r.shape

(6936, 18)